In [1]:
import pandas as pd
import numpy as np
from typing import  Dict, List, Set, Tuple

In [2]:
data = pd.read_csv('data.csv')

C:\Users\nsupakar\AppData\Local\Temp\ipykernel_22028\2948258669.py:1: DtypeWarning: Columns (4,6) have mixed types. Specify dtype option on import or set low_memory=False.
  data = pd.read_csv('data.csv')


In [3]:
## length of data
len(data)

601890

In [4]:
data['slr_id'].nunique()

601890

In [5]:
data.head()

slr_id  parent_seller_id                    xid DAYPHONE phone_cleaned  \
0  1131217717        1131217717  100000000000207809734      NaN           NaN   
1  1374766070        1374766070  100000000000209105581      NaN           NaN   
2  2089517550        2089517550  100000000000809105185      NaN           NaN   
3  1011647251        1011647251  100000000001011647251      NaN           NaN   
4  1593949209        1593949209  100000000001593949209      NaN           NaN   

   ph_cntry_code ph_with_cntry_code  xid_match_id  linked_id  phone_match_id  \
0            NaN                NaN        194174     194174             NaN   
1            NaN                NaN        194694     194694             NaN   
2            NaN                NaN        269874     269874             NaN   
3            NaN                NaN        306889     306889             NaN   
4            NaN                NaN        453506     453506             NaN   

   connected_id  
0             1  
1             1  
2             1  
3             1  
4             1

In [23]:
## CODE SEEMS TO BE WORKING, BUT NOT ALL SELLERS ARE SEEN
# def find_seller_relationships(df: pd.DataFrame) -> Dict[str, List[str]]:
#     """
#     Find all parent-child relationships in a dataset where sellers can be linked 
#     through xid_match_id or phone_match_id across multiple levels.
    
#     Parameters:
#     -----------
#     df : pandas.DataFrame
#         Input dataframe with columns 'Seller_Id', 'xid_match_id', and 'phone_match_id'
    
#     Returns:
#     --------
#     Dict[str, List[str]]
#         A dictionary where each key is a parent seller ID, 
#         and the value is a list of its direct and indirect child seller IDs
#     """
#     # Create a mapping of seller IDs to their potential parents
#     seller_to_parents = {}
#     seller_to_children = {}
    
#     # First, build initial mappings
#     for _, row in df.iterrows():
#         slr_id = row['slr_id']
#         xid_match_id = row['xid_match_id']
#         phone_match_id = row['phone_match_id']
        
#         # Initialize sets for this seller if not already present
#         if slr_id not in seller_to_parents:
#             seller_to_parents[slr_id] = set()
#         if slr_id not in seller_to_children:
#             seller_to_children[slr_id] = set()
        
#         # Find potential parent sellers with matching XID or PID
#         parent_candidates = df[(df['xid_match_id'] == xid_match_id) | (df['phone_match_id'] == phone_match_id)]
        
#         for _, parent_row in parent_candidates.iterrows():
#             parent_id = parent_row['slr_id']
            
#             # Avoid self-referencing
#             if parent_id != slr_id:
#                 seller_to_parents[slr_id].add(parent_id)
#                 seller_to_children[parent_id].add(slr_id)
    
#     def recursive_find_all_children(seller: str, 
#                                      visited: Set[str] = None) -> List[str]:
#         """
#         Recursively find all children of a given seller.
        
#         Parameters:
#         -----------
#         seller : str
#             The seller ID to find children for
#         visited : Set[str], optional
#             Set to track visited sellers and prevent infinite recursion
        
#         Returns:
#         --------
#         List[str]
#             List of all direct and indirect child seller IDs
#         """
#         if visited is None:
#             visited = set()
        
#         # Prevent revisiting sellers to avoid infinite recursion
#         if seller in visited:
#             return []
#         visited.add(seller)
        
#         # Direct children
#         direct_children = seller_to_children.get(seller, set())
        
#         # Recursive children
#         all_children = set(direct_children)
#         for child in direct_children:
#             all_children.update(recursive_find_all_children(child, visited))
        
#         return list(all_children)
    
#     # Compute final relationships
#     relationships = {}
#     for seller in seller_to_children:
#         children = recursive_find_all_children(seller)
#         if children:
#             relationships[seller] = children
    
#     return relationships

# # # Example usage
# # def main():
# #     # Create a sample dataframe
# #     data = {
# #         'Seller_Id': ['A', 'B', 'C', 'D', 'E', 'F'],
# #         'XID': ['X1', 'X1', 'X2', 'X2', 'X3', 'X3'],
# #         'PID': ['P1', 'P1', 'P2', 'P2', 'P3', 'P3']
# #     }
# #     df = pd.DataFrame(data)
    
# #     # Find relationships
# #     relationships = find_seller_relationships(df)
    
# #     # Print results
# #     for parent, children in relationships.items():
# #         print(f"Parent {parent} has children: {children}")

# # if __name__ == "__main__":
# #     main()

In [6]:
data_partial = data[['slr_id', 'xid_match_id','phone_match_id']]

In [7]:
import networkx as nx

In [93]:
def find_linked_seller_ids(df):
    """
    Find linked seller IDs based on XID and PID matches.
    
    Parameters:
    -----------
    df : pandas.DataFrame
        Input DataFrame with columns: Seller_id, XID, PID
    
    Returns:
    --------
    pandas.DataFrame
        DataFrame with columns: Seller_id, Linked_Seller_ids
        Contains all original seller IDs with their linked sellers
    """
    # Create a graph to track connections
    G = nx.Graph()
    
    # Add all seller IDs as nodes initially
    G.add_nodes_from(df['slr_id'].unique())
    
    # First, process XID matches
    xid_groups = df[df['xid_match_id'] != 'N/A'].groupby('xid_match_id')['slr_id'].apply(list)
    for xid_match_id, sellers in xid_groups.items():
        # Connect all sellers with the same XID
        for i in range(len(sellers)):
            for j in range(i+1, len(sellers)):
                G.add_edge(sellers[i], sellers[j])
    
    # Then process PID matches, excluding 'N/A'
    pid_groups = df[df['phone_match_id'] != 'N/A'].groupby('phone_match_id')['slr_id'].apply(list)
    for phone_match_id, sellers in pid_groups.items():
        # Connect all sellers with the same PID
        for i in range(len(sellers)):
            for j in range(i+1, len(sellers)):
                G.add_edge(sellers[i], sellers[j])
    
    # Find connected components (groups of linked sellers)
    connected_components = list(nx.connected_components(G))
    
    # Create a mapping of seller IDs to their linked groups
    seller_links = {}
    for component in connected_components:
        for seller in component:
            # For each seller in a component, store all other sellers in that component
            seller_links[seller] = list(component - {seller})
    
    # # Ensure all original seller IDs are included, even if not linked
    # all_sellers = df['slr_id'].unique()
    # for seller in all_sellers:
    #     if seller not in seller_links:
    #         seller_links[seller] = []
    
    # # Convert to DataFrame
    # result_df = pd.DataFrame.from_dict(seller_links, orient='index', columns=['Linked_Seller_ids'])
    # result_df.index.name = 'slr_id'
    # result_df.reset_index(inplace=True)
    
    return seller_links

# # Example usage
# # Create a sample DataFrame
# data = {
#     'Seller_id': ['A', 'B', 'C', 'D', 'E', 'F'],
#     'XID': ['X1', 'X1', 'X2', 'X3', 'N/A', 'N/A'],
#     'PID': ['P1', 'P2', 'P2', 'N/A', 'P3', 'P3']
# }
# df = pd.DataFrame(data)

In [ ]:
    xid_groups = data_partial[data_partial['xid_match_id'] != 'N/A'].groupby('xid_match_id')['slr_id'].apply(list)


In [94]:
results = find_linked_seller_ids(data_partial)

In [95]:
len(results)

601890

In [97]:
df_linked = pd.DataFrame(results.items(), columns = ('slr_id','linked_sellers')) 

In [100]:
## unique values
df_linked['slr_id'].nunique()

601890

In [101]:
df_linked.to_csv('linked_all_sellers.csv')

In [102]:
results

{np.int64(1131217717): [],
 np.int64(1374766070): [],
 np.int64(2089517550): [],
 np.int64(1011647251): [],
 np.int64(1593949209): [],
 np.int64(1913438005): [],
 np.int64(2160854661): [],
 np.int64(2049969732): [],
 np.int64(2457566594): [],
 np.int64(2575639803): [],
 np.int64(123328): [],
 np.int64(161709): [],
 np.int64(569150): [],
 np.int64(2334882105): [],
 np.int64(1089621): [],
 np.int64(1204464): [],
 np.int64(1270240): [],
 np.int64(1310225): [],
 np.int64(1584612): [],
 np.int64(1806109): [],
 np.int64(1817950): [],
 np.int64(1950341): [],
 np.int64(1812453471): [],
 np.int64(2102099): [],
 np.int64(2168637): [],
 np.int64(2179787): [],
 np.int64(2235074): [],
 np.int64(2305420): [],
 np.int64(2362749): [],
 np.int64(2835401): [],
 np.int64(2945607): [],
 np.int64(3034504): [],
 np.int64(3412175): [],
 np.int64(2396959991): [],
 np.int64(3712207): [],
 1290052012: [np.int64(3862509)],
 np.int64(3862509): [1290052012],
 np.int64(3911737): [],
 np.int64(4113866): [],
 np.int6

In [103]:
## saving dictionary
with open('linked_all_sellers.pkl', 'wb') as fp:
    pickle.dump(results, fp)
    print('dictionary saved successfully to file')

dictionary saved successfully to file


In [113]:
df_linked.columns

Index(['slr_id', 'linked_sellers'], dtype='object')

In [114]:
az

KeyError: 'linked_sellers'

: 

In [76]:
# # Example usage
# def main():
#     # Create a sample dataframe
    
    
#     # Find relationships
#     relationships = find_seller_relationships(data_partial)
    
#     # Print results
#     for parent, children in relationships.items():
#         print(f"Parent {parent} has children: {children}")

# # if __name__ == "__main__":
# #     main()

In [86]:
df= pd.DataFrame(results.items()) 

In [90]:
df[df[0]==1371889023]

0                                                  1
50167  1371889023  [2480785186, 2443751587, 2439056805, 242687248...

In [8]:

def find_linked_sellers(df):
    """
    Find all seller IDs that are linked through shared XIDs or PIDs.
    
    Parameters:
    df (pandas.DataFrame): DataFrame with columns 'Seller_id', 'XID', and 'PID'
    
    Returns:
    dict: A dictionary where keys are seller IDs and values are sets of linked seller IDs
    """
    # Create a graph to represent seller connections
    G = nx.Graph()
    
    # Add edges based on shared XIDs
    for xid_match_id in df['xid_match_id'].unique():
        # Find sellers with this XID
        sellers_with_xid = df[df['xid_match_id'] == xid_match_id]['slr_id'].unique()
        
        # Connect all these sellers in the graph
        for i in range(len(sellers_with_xid)):
            for j in range(i+1, len(sellers_with_xid)):
                G.add_edge(sellers_with_xid[i], sellers_with_xid[j])
    
    # Add edges based on shared PIDs
    for phone_match_id in df['phone_match_id'].unique():
        # Find sellers with this PID
        if (phone_match_id == "N/A"):
            continue
        sellers_with_pid = df[df['phone_match_id'] == phone_match_id]['slr_id'].unique()
        
        # Connect all these sellers in the graph
        for i in range(len(sellers_with_pid)):
            for j in range(i+1, len(sellers_with_pid)):
                G.add_edge(sellers_with_pid[i], sellers_with_pid[j])
    
    # Find connected components (groups of linked sellers)
    linked_sellers = {}
    for component in nx.connected_components(G):
        # For each seller in the component, store the entire set of linked sellers
        for seller in component:
            linked_sellers[seller] = component - {seller}
    
    return linked_sellers


In [29]:
def demonstrate_usage():
    # Create a sample DataFrame
    
    
    
    # Find linked sellers
    seller_links = find_linked_sellers(partial_data)
    
    # Print results
    print("Seller ID Linkages:")
    for seller, links in seller_links.items():
        print(f"Seller {seller} is linked to: {links}")

In [9]:
seller_links = find_linked_sellers(data_partial)


In [11]:
df= pd.DataFrame(seller_links.items()) 

In [13]:
len(df)

78349

In [14]:
df.to_csv('only_sellers_linked.csv')

In [15]:
df.to_csv('only_sellers_linked_2.csv')

In [53]:
import pickle

## saving dictionary
with open('seller_links.pkl', 'wb') as fp:
    pickle.dump(seller_links, fp)
    print('dictionary saved successfully to file')

dictionary saved successfully to file


In [55]:
## reading a dictionary
with open('seller_links.pkl', 'rb') as fp:
    links = pickle.load(fp)
    print('Person dictionary')
    print(person)

Person dictionary
{np.int64(1290052012): {np.int64(3862509)}, np.int64(3862509): {np.int64(1290052012)}, np.int64(4528155): {np.int64(1488855031)}, np.int64(1488855031): {np.int64(4528155)}, np.int64(7539888): {np.int64(1930602712)}, np.int64(1930602712): {np.int64(7539888)}, np.int64(7955074): {np.int64(1168462845)}, np.int64(1168462845): {np.int64(7955074)}, np.int64(8754464): {np.int64(183055782)}, np.int64(183055782): {np.int64(8754464)}, np.int64(9215425): {np.int64(1006280879)}, np.int64(1006280879): {np.int64(9215425)}, np.int64(2478992874): {np.int64(2080608379)}, np.int64(2080608379): {np.int64(2478992874)}, np.int64(845894738): {np.int64(14447971)}, np.int64(14447971): {np.int64(845894738)}, np.int64(993896155): {np.int64(20159996)}, np.int64(20159996): {np.int64(993896155)}, np.int64(24854320): {np.int64(148176281)}, np.int64(148176281): {np.int64(24854320)}, np.int64(2423500648): {np.int64(25152331)}, np.int64(25152331): {np.int64(2423500648)}, np.int64(25685736): {np.int64

In [43]:
data_partial = data[['slr_id', 'xid_match_id','phone_match_id']]

In [56]:
person


{np.int64(1290052012): {np.int64(3862509)},
 np.int64(3862509): {np.int64(1290052012)},
 np.int64(4528155): {np.int64(1488855031)},
 np.int64(1488855031): {np.int64(4528155)},
 np.int64(7539888): {np.int64(1930602712)},
 np.int64(1930602712): {np.int64(7539888)},
 np.int64(7955074): {np.int64(1168462845)},
 np.int64(1168462845): {np.int64(7955074)},
 np.int64(8754464): {np.int64(183055782)},
 np.int64(183055782): {np.int64(8754464)},
 np.int64(9215425): {np.int64(1006280879)},
 np.int64(1006280879): {np.int64(9215425)},
 np.int64(2478992874): {np.int64(2080608379)},
 np.int64(2080608379): {np.int64(2478992874)},
 np.int64(845894738): {np.int64(14447971)},
 np.int64(14447971): {np.int64(845894738)},
 np.int64(993896155): {np.int64(20159996)},
 np.int64(20159996): {np.int64(993896155)},
 np.int64(24854320): {np.int64(148176281)},
 np.int64(148176281): {np.int64(24854320)},
 np.int64(2423500648): {np.int64(25152331)},
 np.int64(25152331): {np.int64(2423500648)},
 np.int64(25685736): {np.i

In [91]:
df= pd.DataFrame(seller_links.items()) 

In [92]:
## length of dictionary
df[df[0]==1371889023]

0                                                  1
5297  1371889023  {2480785186, 2443751587, 2439056805, 242687248...

In [60]:
seller_links.items()

dict_items([(np.int64(1290052012), {np.int64(3862509)}), (np.int64(3862509), {np.int64(1290052012)}), (np.int64(4528155), {np.int64(1488855031)}), (np.int64(1488855031), {np.int64(4528155)}), (np.int64(7539888), {np.int64(1930602712)}), (np.int64(1930602712), {np.int64(7539888)}), (np.int64(7955074), {np.int64(1168462845)}), (np.int64(1168462845), {np.int64(7955074)}), (np.int64(8754464), {np.int64(183055782)}), (np.int64(183055782), {np.int64(8754464)}), (np.int64(9215425), {np.int64(1006280879)}), (np.int64(1006280879), {np.int64(9215425)}), (np.int64(2478992874), {np.int64(2080608379)}), (np.int64(2080608379), {np.int64(2478992874)}), (np.int64(845894738), {np.int64(14447971)}), (np.int64(14447971), {np.int64(845894738)}), (np.int64(993896155), {np.int64(20159996)}), (np.int64(20159996), {np.int64(993896155)}), (np.int64(24854320), {np.int64(148176281)}), (np.int64(148176281), {np.int64(24854320)}), (np.int64(2423500648), {np.int64(25152331)}), (np.int64(25152331), {np.int64(2423500

In [61]:
df= pd.DataFrame(seller_links.items()) 

In [64]:
df.head()

0             1
0  1290052012     {3862509}
1     3862509  {1290052012}
2     4528155  {1488855031}
3  1488855031     {4528155}
4     7539888  {1930602712}

In [66]:
df[df[0]== 994045793]

0                       1
23  994045793  {25685736, 1645751828}